In [1]:
import torch
print(torch.cuda.is_available())

True


In [2]:
from sentence_transformers import SentenceTransformer
import numpy as np

embedding_model_name = "jhgan/ko-sbert-sts"
embedding = SentenceTransformer(embedding_model_name)

# pred_embeddings = embedding.encode(test_results)

/home/aicontest/anaconda3/envs/construct/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2025-03-27 09:33:13.927932: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-03-27 09:33:13.936216: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1743035593.945386 2067581 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1743035593.948108 2067581 cuda_bla

In [3]:

def cosine_similarity(a, b):
    """코사인 유사도 계산"""
    dot_product = np.dot(a, b)
    norm_a = np.linalg.norm(a)
    norm_b = np.linalg.norm(b)
    return dot_product / (norm_a * norm_b) if norm_a != 0 and norm_b != 0 else 0


def jaccard_similarity(text1, text2):
    """자카드 유사도 계산"""
    set1, set2 = set(text1.split()), set(text2.split())  # 단어 집합 생성
    intersection = len(set1.intersection(set2))  # 교집합 크기
    union = len(set1.union(set2))  # 합집합 크기
    return intersection / union if union != 0 else 0

In [9]:
question = "다음 상황을 가정해 봅시다. 작업프로세스 '조립작업' 도중에 [인적사고: 기타 / 물적사고: 전도]가 보고되었습니다. 사고객체는 부재 (중분류: 교각 기초)이고 사고 원인은 교각 기초철근 조립 중 강한 바람에 의해 기둥측 주철근이 균형을 잃고 전도되어, 하부에서 작업 중이던 철근공 2명이 철근에 부딪힌 사고입니다. 이러한 사고에 대해 재발을 막고 피해를 최소화하기 위한 방안은 무엇일까요?"
chosen = "위험성 평가 및 교육을 통해 작업장 내 위험요인과 안전수칙을 근로자에게 전파하고, 근로자 안전교육을 강화하며, 본 사고와 관련된 유사 피해 발생 방지를 위한 안전교육을 실시할 계획."
reject = "근로자 안전교육 실시와 공사장 안전관리 철저 지도를 통한 동일한 사고 발생 방지 대책 마련."

Q = embedding.encode(question)
A1 = embedding.encode(chosen)
A2 = embedding.encode(reject)

good = cosine_similarity(Q, A1) # * 0.7 + 0.3 * jaccard_similarity(question, chosen)
bad = cosine_similarity(Q, A2) # * 0.7 + 0.3 * jaccard_similarity(question, reject)

print(f"good score : {good}, bad score : {bad}")

good score : 0.3910810053348541, bad score : 0.28459566831588745


prompt /  train 재발 방지 대책 및 향후조치계획의 정답  / 
이거 두개의 cosine 유사도 평균 구하기 

train 데이터 한 개당 prompt 여러개 ,  각각의 score 를 구해서 평균구하기 
다시 평균 내서 threshold 정하기

In [ ]:
# 1. train csv 불러오기 -> 재발방지 대책 및 향후조치 계획 뽑아서 저장
# 2. prompt 10개랑 train 재발 방지 대책 및 향후조치계획 column 값이랑 cosine 유사도 구하기 
# 3. 이 때 데이터 한 개 마다 10개의 프롬포트랑 유사도 구하고 , train 데이터 전체에 대해 각각 모두 구했으면 이를 평균내서 전체 cosine similarity 구하기 


In [5]:
import pandas as pd
import numpy as np
from sentence_transformers import SentenceTransformer

# 임베딩 모델 로드
embedding_model_name = "jhgan/ko-sbert-sts"
model = SentenceTransformer(embedding_model_name)

def cosine_similarity(a, b):
    """코사인 유사도 계산"""
    dot_product = np.dot(a, b)
    norm_a = np.linalg.norm(a)
    norm_b = np.linalg.norm(b)
    return dot_product / (norm_a * norm_b) if (norm_a != 0 and norm_b != 0) else 0

def generate_prompts(row):
    """
    row(Series)에서 필요한 컬럼값을 꺼내 
    1~10번 템플릿에 맞춰 질문 리스트를 리턴한다.
    """
    
    # 1~3: 사고원인만 사용
    question1 = f"사고 원인은 '{row['사고원인']}'이다. 어떻게 해야 하는가?"
    question2 = f"이번 사고의 원인은 '{row['사고원인']}'이다. 어떻게 예방해야 하는가?"
    question3 = f"사고 원인이 '{row['사고원인']}'인 상황이다. 어떤 대책이 필요한가?"

    # 4~7: 작업프로세스 / 인적사고 / 사고객체 / 사고원인
    #     (※ 사고객체(대분류), 사고객체(중분류)를 이미 전처리해서 갖고 있다고 가정)
    question4 = (
        f"'{row['작업프로세스']}' 중 '{row['인적사고']}' 사고 발생. "
        + f"사고 객체: {row['사고객체(대분류)']}({row['사고객체(중분류)']}). "
        + f"이 때 사고 원인은 '{row['사고원인']}'이다."
        + "어떻게 해야 하는가?"
    )
    question5 = (
        f"작업 '{row['작업프로세스']}' 도중 '{row['인적사고']}' 사고가 발생했다. "
        + f"사고 객체: {row['사고객체(대분류)']}({row['사고객체(중분류)']}). "
        + f"이 때 사고 원인은 '{row['사고원인']}'이다."
        + "예방 방안은 무엇인가?"
    )
    question6 = (
        f"{row['작업프로세스']} 도중 '{row['인적사고']}' 사고가 났다. "
        + f"사고 객체: {row['사고객체(대분류)']}({row['사고객체(중분류)']}). "
        + f"이 때 사고 원인은 '{row['사고원인']}'이다."
        + "어떤 조치를 취해야 하는가?"
    )
    question7 = (
        f"작업프로세스 '{row['작업프로세스']}', 인적사고: '{row['인적사고']}', "
        + f"사고 객체: {row['사고객체(대분류)']}({row['사고객체(중분류)']}). "
        + f"이 때 사고 원인은 '{row['사고원인']}'이다."
        + "대응책은 무엇인가?"
    )

    # 8~10: 공사종류 / 인적사고 / 공종 / 사고객체 / 작업프로세스
    #       / 사고원인 / 장소 / 부위 모두 사용
    question8 = (
        f"공사종류: {row['공사종류']}, 공종: {row['공종']}, 장소: {row['장소']}, "
        f"사고 부위: {row['부위']}. "
        + f"작업 현장에서 {row['인적사고']} 인적사고"
        + (f"와 {row['물적사고']} 물적사고가 동시에" if row['물적사고'] != '없음' else "가")
        + " 발생했다. "
        + f"사고 객체는 {row['사고객체(대분류)']}({row['사고객체(중분류)']})이며, "
        + f"사고 원인은 '{row['사고원인']}'이다. "
        + f"{row['작업프로세스']} 상황에서 이러한 사고를 방지하기 위해 "
        + "어떤 대책과 조치를 마련해야 하는가?"
    )

    question9 = (
        f"공사종류: {row['공사종류']}, 공종: {row['공종']}, 장소: {row['장소']}, "
        f"사고 부위: {row['부위']}. "
        f"'{row['작업프로세스']}' 과정 중 '{row['인적사고']}' 사고가 발생했다. "
        f"사고 객체: {row['사고객체(대분류)']}({row['사고객체(중분류)']}), "
        f"사고 원인은 '{row['사고원인']}'이다. "
        "위험을 줄이기 위해 어떤 조치를 취해야 하는가?"
    )

    question10 = (
        f"공사종류: {row['공사종류']}, 공종: {row['공종']}, 장소: {row['장소']}, "
        f"사고 부위: {row['부위']}. "
        + f"{row['인적사고']} 인적사고"
        + (f", {row['물적사고']} 물적사고가" if row['물적사고'] != '없음' else "가")
        + " 발생했다. "
        + f"사고 객체는 {row['사고객체(대분류)']}({row['사고객체(중분류)']})이며, "
        + f"{row['작업프로세스']} 중 발생한 사고 원인은 '{row['사고원인']}'이다. "
        + "재발 방지 및 조치 계획을 어떻게 세워야 하는가?"
    )

    return [
        question1, question2, question3,
        question4, question5, question6, question7,
        question8, question9, question10
    ]

# -----------------------------
# 실제 코드 시작
# -----------------------------

from tqdm import tqdm
if __name__ == "__main__":
    # CSV 불러오기
    train_dir = '/home/aicontest/construct/data/train.csv'
    train_df = pd.read_csv(train_dir)

    train_df['장소(대)'] =train_df['장소'].str.split(' / ').str[0].fillna("")
    train_df['장소(소)'] =train_df['장소'].str.split(' / ').str[1].fillna("")
    train_df['공사종류(대분류)'] =train_df['공사종류'].str.split(' / ').str[0].fillna("")
    train_df['공사종류(중분류)'] =train_df['공사종류'].str.split(' / ').str[1].fillna("")
    train_df['공종(대분류)'] =train_df['공종'].str.split(' > ').str[0].fillna("")
    train_df['공종(중분류)'] =train_df['공종'].str.split(' > ').str[1].fillna("")
    train_df['사고객체(대분류)'] =train_df['사고객체'].str.split(' > ').str[0].fillna("")
    train_df['사고객체(중분류)'] =train_df['사고객체'].str.split(' > ').str[1].fillna("")
    train_df['부위(대)'] =train_df['부위'].str.split(' / ').str[0].fillna("")
    train_df['부위(소)'] =train_df['부위'].str.split(' / ').str[1].fillna("")

    # 각 row별 유사도 평균을 저장할 리스트
    row_similarities = []

    for idx, row in tqdm(train_df.iterrows(), total=len(train_df), desc='mean QA similarity'):
        # 1) 템플릿 1~10개 생성
        prompts = f"{row['사고원인']}"

        # 2) answer(재발방지대책 및 향후조치계획) 불러오기
        answer_text = row["재발방지대책 및 향후조치계획"]

        # 3) 임베딩 계산
        answer_embedding = model.encode(answer_text)
        prompt_embedding = model.encode(prompts)
        sim = cosine_similarity(prompt_embedding, answer_embedding)

        # prompt_sims = []
        # for prompt in prompts:
        #     prompt_embedding = model.encode(prompt)
        #     sim = cosine_similarity(prompt_embedding, answer_embedding)
        #     prompt_sims.append(sim)

        # 4) 해당 row의 프롬프트-정답 유사도 평균
        # row_avg_sim = np.mean(prompt_sims)
        # row_similarities.append(row_avg_sim)

        row_similarities.append(sim)

    # 5) 전체 row에 대한 평균 유사도
    overall_avg_similarity = np.mean(row_similarities)

    print(f"전체 row 평균 유사도: {overall_avg_similarity:.4f}")


mean QA similarity: 100%|██████████| 23422/23422 [02:34<00:00, 151.24it/s]

전체 row 평균 유사도: 0.3483


In [6]:
best_answer = None
best_score = -1

output_list = train_df['재발방지대책 및 향후조치계획'].tolist()
embeddings = model.encode(output_list)

score = []
for i, answer1 in tqdm(enumerate(output_list), total=len(output_list)):
    total_score = 0
    for j, answer2 in enumerate(output_list):
        if i != j:
            # 코사인 유사도
            cosine_sim = cosine_similarity(embeddings[i], embeddings[j]).item()

            # 최종 유사도: 0.7 * 코사인 유사도 + 0.3 * 자카드 유사도
            total_score += cosine_sim

    # 평균 유사도가 가장 높은 문장을 선택
    avg_score = total_score / (len(output_list) - 1)  # 자기 자신 제외
    score.append(avg_score)
    if avg_score > best_score:
        best_score = avg_score
        best_answer = answer1

print(best_answer, best_score)
sorted_indices = np.argsort(score)[::-1]
top5_indices = sorted_indices[:5]
for idx in top5_indices:
    print(f"Index: {idx}, Value: {output_list[idx]}")


100%|██████████| 23422/23422 [39:26<00:00,  9.90it/s]


작업전 안전교육 강화 및 작업장 위험요소 점검을 통한 재발 방지와 안전관리 교육 철저를 통한 향후 조치 계획. 0.6754812563817912
Index: 13132, Value: 작업전 안전교육 강화 및 작업장 위험요소 점검을 통한 재발 방지와 안전관리 교육 철저를 통한 향후 조치 계획.
Index: 22875, Value: 안전교육 실시와 작업 중 안전관리 철저를 통한 재발 방지 대책 및 향후 조치 계획.
Index: 10573, Value: 작업전 안전교육 실시와 안전관리자 안전점검 실시를 통한 재발 방지 대책 및 향후 조치 계획.
Index: 12528, Value: 작업자 안전교육 실시와 작업 위험구간 안전조치 철저, 안전점검 및 안전조치 여부 전수 확인을 통한 유사사고 예방.
Index: 10901, Value: 작업 전 위험사항 전파 및 교육 철저와 사고 예방을 위한 관리감독자 및 작업자 교육 강화, 점검을 통한 안전관리 실시.


In [7]:
print(np.mean(score))

0.5315393871518644


In [8]:
print(best_answer, best_score)
sorted_indices = np.argsort(score)[::-1]
top5_indices = sorted_indices
for idx in top5_indices:
    print(f"Index: {idx}, Value: {output_list[idx]}, score: {score[idx]}")

작업전 안전교육 강화 및 작업장 위험요소 점검을 통한 재발 방지와 안전관리 교육 철저를 통한 향후 조치 계획. 0.6754812739290363
Index: 13132, Value: 작업전 안전교육 강화 및 작업장 위험요소 점검을 통한 재발 방지와 안전관리 교육 철저를 통한 향후 조치 계획., score: 0.6754812739290363
Index: 22875, Value: 안전교육 실시와 작업 중 안전관리 철저를 통한 재발 방지 대책 및 향후 조치 계획., score: 0.666300920365009
Index: 10573, Value: 작업전 안전교육 실시와 안전관리자 안전점검 실시를 통한 재발 방지 대책 및 향후 조치 계획., score: 0.6659276302027324
Index: 12528, Value: 작업자 안전교육 실시와 작업 위험구간 안전조치 철저, 안전점검 및 안전조치 여부 전수 확인을 통한 유사사고 예방., score: 0.6658516157879598
Index: 10901, Value: 작업 전 위험사항 전파 및 교육 철저와 사고 예방을 위한 관리감독자 및 작업자 교육 강화, 점검을 통한 안전관리 실시., score: 0.6650807003478578
Index: 14484, Value: 안전교육 실시와 작업 시 안전관리 철저를 통한 재발 방지 대책 및 향후 조치 계획., score: 0.6644570715078058
Index: 14529, Value: 안전교육 실시와 현장 내 작업지시사항 철저 이행, 안전관리 교육 이행, 안전위험요소 제거 점검 및 대책 강구를 통한 재발 방지 대책., score: 0.6625861595018347
Index: 4319, Value: 작업전 안전교육 실시, 작업수칙 준수, 기계공구류 안전장치 확인을 통한 재발 방지 대책 및 향후 조치 계획., score: 0.6621997825043303
Index: 21434, Value: 작업전 안전교육 실시, 안전시설 재점검, 안전장구류 착용 철저 등의 재발 

test.csv 로 prompt 구성 (10개) , 이에 대한 답변인 baseline_submission.csv 의 재발방지및향후조치계획 이 answer 가 됨 
이 두개의 cosine 유사도 위와 동일한 방법으로 비교, threshold 0.4050 를 넘으면 true, 그렇지 않으면 false 

전체에서 true 나온 갯수 (accuracy)

In [5]:
import pandas as pd
import numpy as np
from sentence_transformers import SentenceTransformer
from tqdm import tqdm  # 진행률 표시 라이브러리

# ----- 1) 전처리 및 모델 로드 -----
embedding_model_name = "jhgan/ko-sbert-sts"
model = SentenceTransformer(embedding_model_name)

def cosine_similarity(a, b):
    dot_product = np.dot(a, b)
    norm_a = np.linalg.norm(a)
    norm_b = np.linalg.norm(b)
    return dot_product / (norm_a * norm_b) if (norm_a != 0 and norm_b != 0) else 0

def generate_prompts(row):
    """
    test.csv의 row(Series)를 받아 템플릿 1~10개의 질문을 생성해 리턴
    (사고객체(대분류), 사고객체(중분류)가 row에 있다고 가정)
    """
    # 1~3: 사고원인
    question1 = f"사고 원인은 '{row['사고원인']}'이다. 어떻게 해야 하는가?"
    question2 = f"이번 사고의 원인은 '{row['사고원인']}'이다. 어떻게 예방해야 하는가?"
    question3 = f"사고 원인이 '{row['사고원인']}'인 상황이다. 어떤 대책이 필요한가?"

    # 4~7: 작업프로세스 / 인적사고 / 사고객체 / 사고원인
    question4 = (
        f"'{row['작업프로세스']}' 중 '{row['인적사고']}' 사고 발생. "
        + f"사고 객체: {row['사고객체(대분류)']}({row['사고객체(중분류)']}). "
        + f"이 때 사고 원인은 '{row['사고원인']}'이다."
        + "어떻게 해야 하는가?"
    )
    question5 = (
        f"작업 '{row['작업프로세스']}' 도중 '{row['인적사고']}' 사고가 발생했다. "
        + f"사고 객체: {row['사고객체(대분류)']}({row['사고객체(중분류)']}). "
        + f"이 때 사고 원인은 '{row['사고원인']}'이다."
        + "예방 방안은 무엇인가?"
    )
    question6 = (
        f"{row['작업프로세스']} 도중 '{row['인적사고']}' 사고가 났다. "
        + f"사고 객체: {row['사고객체(대분류)']}({row['사고객체(중분류)']}). "
        + f"이 때 사고 원인은 '{row['사고원인']}'이다."
        + "어떤 조치를 취해야 하는가?"
    )
    question7 = (
        f"작업프로세스 '{row['작업프로세스']}', 인적사고: '{row['인적사고']}', "
        + f"사고 객체: {row['사고객체(대분류)']}({row['사고객체(중분류)']}). "
        + f"이 때 사고 원인은 '{row['사고원인']}'이다."
        + "대응책은 무엇인가?"
    )

    # 8~10: 공사종류 / 인적사고 / 공종 / 사고객체 / 작업프로세스 / 사고원인 / 장소 / 부위
    question8 = (
        f"공사종류: {row['공사종류']}, 공종: {row['공종']}, 장소: {row['장소']}, "
        f"사고 부위: {row['부위']}. "
        + f"작업 현장에서 {row['인적사고']} 인적사고"
        + (f"와 {row['물적사고']} 물적사고가 동시에" if row['물적사고'] != '없음' else "가")
        + " 발생했다. "
        + f"사고 객체는 {row['사고객체(대분류)']}({row['사고객체(중분류)']})이며, "
        + f"사고 원인은 '{row['사고원인']}'이다. "
        + f"{row['작업프로세스']} 상황에서 이러한 사고를 방지하기 위해 "
        + "어떤 대책과 조치를 마련해야 하는가?"
    )

    question9 = (
        f"공사종류: {row['공사종류']}, 공종: {row['공종']}, 장소: {row['장소']}, "
        f"사고 부위: {row['부위']}. "
        f"'{row['작업프로세스']}' 과정 중 '{row['인적사고']}' 사고가 발생했다. "
        f"사고 객체: {row['사고객체(대분류)']}({row['사고객체(중분류)']}), "
        f"사고 원인은 '{row['사고원인']}'이다. "
        "위험을 줄이기 위해 어떤 조치를 취해야 하는가?"
    )

    question10 = (
        f"공사종류: {row['공사종류']}, 공종: {row['공종']}, 장소: {row['장소']}, "
        f"사고 부위: {row['부위']}. "
        + f"{row['인적사고']} 인적사고"
        + (f", {row['물적사고']} 물적사고가" if row['물적사고'] != '없음' else "가")
        + " 발생했다. "
        + f"사고 객체는 {row['사고객체(대분류)']}({row['사고객체(중분류)']})이며, "
        + f"{row['작업프로세스']} 중 발생한 사고 원인은 '{row['사고원인']}'이다. "
        + "재발 방지 및 조치 계획을 어떻게 세워야 하는가?"
    )

    return [
        question1, question2, question3,
        question4, question5, question6, question7,
        question8, question9, question10
    ]

if __name__ == "__main__":
    # ----- 2) 파일 불러오기 -----
    test_path = "/home/aicontest/construct/data/test.csv"
    sub_path = "/home/aicontest/construct/experiment/result/baseline_submission_RAG.csv"
    
    test_df = pd.read_csv(test_path)
    sub_df = pd.read_csv(sub_path)
    
    test_df['장소(대)'] =test_df['장소'].str.split(' / ').str[0].fillna("")
    test_df['장소(소)'] =test_df['장소'].str.split(' / ').str[1].fillna("")
    test_df['공사종류(대분류)'] =test_df['공사종류'].str.split(' / ').str[0].fillna("")
    test_df['공사종류(중분류)'] =test_df['공사종류'].str.split(' / ').str[1].fillna("")
    test_df['공종(대분류)'] =test_df['공종'].str.split(' > ').str[0].fillna("")
    test_df['공종(중분류)'] =test_df['공종'].str.split(' > ').str[1].fillna("")
    test_df['사고객체(대분류)'] =test_df['사고객체'].str.split(' > ').str[0].fillna("")
    test_df['사고객체(중분류)'] =test_df['사고객체'].str.split(' > ').str[1].fillna("")
    test_df['부위(대)'] =test_df['부위'].str.split(' / ').str[0].fillna("")
    test_df['부위(소)'] =test_df['부위'].str.split(' / ').str[1].fillna("")

    # 두 DF가 row 개수와 대응이 맞다고 가정 (예: 인덱스 0~N 동일)
    
    THRESHOLD = 0.4050
    true_count = 0  # threshold를 넘은 케이스 수
    avg = 0
    for idx, test_row in tqdm(test_df.iterrows(), total=len(test_df), desc="Processing rows"):
        # 1) test.csv 로 prompt 구성
        prompts = generate_prompts(test_row)

        # 2) baseline_submission.csv 의 답변 (answer)
        answer_text = sub_df.iloc[idx]["재발방지대책 및 향후조치계획"]
        #answer_text = sub_df.loc[idx, "재발방지대책 및 향후조치계획"]
        # 3) 임베딩 후 코사인 유사도 계산
        answer_emb = model.encode(answer_text)

        sims = []
        for prompt in prompts:
            prompt_emb = model.encode(prompt)
            sim = cosine_similarity(prompt_emb, answer_emb)
            sims.append(sim)

        # row의 유사도 평균
        avg_sim = np.mean(sims)
        avg += avg_sim
        # threshold 넘는지 확인
        if avg_sim >= THRESHOLD:
            true_count += 1

    # 4) Accuracy (전체 중 threshold 초과한 케이스 비율)
    total_rows = len(test_df)
    avg = avg / total_rows
    accuracy = true_count / total_rows

    print(f"Threshold = {THRESHOLD}")
    print(f"True(>=threshold) count: {true_count}")
    print(f"avg score : {avg:.4f}")
    print(f"Accuracy: {accuracy:.4f}")


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
Processing rows: 100%|██████████| 964/964 [00:38<00:00, 25.18it/s]

Threshold = 0.405
True(>=threshold) count: 476
avg score : 0.4114
Accuracy: 0.4938


정확도가 클수록 맥락이 잘 맞는다 (구체적임 , 덜 general )
